In [1]:
import pandas as pd
import altair as alt
alt.data_transformers.disable_max_rows() # Disable 5_000 rows limit
findings_data = pd.read_csv("https://code4rena.com/community-resources/findings.csv")
contests_data = pd.read_csv("https://code4rena.com/community-resources/contests.csv")

In [2]:
findings_data["finding"].str[0].unique()

array(['G', 'H', 'L', 'M', 'N', nan, 'Q', 'A'], dtype=object)

In [3]:
categories_labels = {'H': "High", 'M': "Medium", 'L': "Low", 'A': "Analysis", 'Q': "QA", 'G': "Gas"}
label_colors = ["#FE266D","#FA6C44","#F2E713","#D1D811","#0AB6F8","#5688C1"]
df = findings_data[findings_data["finding"].str[0].isin(categories_labels)]

In [4]:
df["finding"].str[0].unique()

array(['G', 'H', 'L', 'M', 'Q', 'A'], dtype=object)

In [5]:
df["finding_category"] = df["finding"].str[0].apply(categories_labels.get)

/tmp/ipykernel_41009/601229947.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["finding_category"] = df["finding"].str[0].apply(categories_labels.get)


In [6]:
split_slider = alt.binding_range(min=1, max=df["split"].max(), step=1, name="Maximum number of wardens sharing a finding")
split_slider_selection = alt.param(bind=split_slider, value=1)

In [7]:
alt.Chart(
    df,
    width=500,
    height=500,
    title="Average finding reward by categories"
).transform_filter(
    alt.datum.split <= split_slider_selection
).transform_aggregate(
    total_awards='mean(awardUSD)',
    groupby=['finding_category']
).mark_arc(
).encode(
    theta=alt.Theta("total_awards:Q"),
    color=alt.Color(
        "finding_category:O",
        scale=alt.Scale(
            domain=list(categories_labels.values()),
            range=label_colors,
        ),
        legend=alt.Legend(title="Categories")
    ),
    order=alt.Order("total_awards:Q", sort="descending"),
    tooltip=["total_awards:Q", "finding_category"]
).add_params(
    split_slider_selection
)

alt.Chart(...)